# Fedora UBI micro コンテナ生成

In [1]:
import json
import sys

RELEASE_VER = '41'
WK_CTN_NAME = 'wk-con'
NEW_CTN_NAME = f'fedora{RELEASE_VER}-micro'
#NEW_CTN_NAME = f'fedora{RELEASE_VER}-minimal'
DNF_CMD = 'dnf'
DNF_CACHE = f'dnfcache/{RELEASE_VER}'
DNF_DOWNLOAD_PROGRESS_OUTPUT = False

LF_DNF_CMD_DISTRO_SYNC = lambda wk_mnt, dnf_repos : \
f'''{DNF_CMD} distro-sync \\
    --use-host-config \\
    --releasever {RELEASE_VER} \\
    --installroot '{wk_mnt}/' \\
    --setopt install_weak_deps=false \\
    --nodocs \\
    --setopt cachedir='{DNF_CACHE}' \\
    --disablerepo='*' --enablerepo='{" ".join(dnf_repos)}'{' 2>/dev/null' if not DNF_DOWNLOAD_PROGRESS_OUTPUT else ''}
'''

SEP = '=' * 10

dnf_repos = set((
    'fedora',
#    'fedora-cisco-openh264',
    'updates',
))
#dnf_repos = set((
#    'fedora.enabled=1',
#    'fedora-cisco-openh264.enabled=0',
#    'updates.enabled=1',
#))

if NEW_CTN_NAME.endswith('-micro'):
    inst_pkgs = set((
        'coreutils-single',
    #    'glibc-all-langpacks',
    #    'glibc-langpack-en',
        'glibc-minimal-langpack',
    #    'systemd',
    #    'python311', 'python3-pip',
    #    'zsh', 'util-linux', 'util-linux-user', 'which', 'git',
    #    'util-linux-core', # mount
    #    'iputils', # ping
    #    'net-tools', 'bind-utils', 'rsync', 'curl', 'sudo',
    ))
elif NEW_CTN_NAME.endswith('-minimal'):
    inst_pkgs = set((
        'coreutils-single',
    #    'glibc-all-langpacks',
    #    'glibc-langpack-en',
        'glibc-minimal-langpack',
        'bash',
        'curl' if int(RELEASE_VER) >= 41 
            else 'curl-minimal', # https://fedoraproject.org/wiki/Changes/CurlMinimal_as_Default
        'libcurl-minimal',
        'libusbx',
        'dnf',
    #    'systemd',
    #    'python311', 'python3-pip',
    #    'zsh', 'util-linux', 'util-linux-user', 'which', 'git',
    #    'util-linux-core', # mount
    #    'iputils', # ping
    #    'net-tools', 'bind-utils', 'rsync', 'curl', 'sudo',
    ))
    reinst_pkgs = set((
        'krb5-libs',
    ))

ctns_json = !buildah containers --json
ctns = json.loads(ctns_json.n) if ctns_json.n != 'null' else []

if len(ctns) != 0 and \
   len([ctn['containername'] for ctn in ctns if ctn['containername'] == WK_CTN_NAME]) != 0:
    # Deal with directory not empty error
    wk_mnt = !buildah unshare buildah mount {WK_CTN_NAME}
    !buildah unshare rm -rf {wk_mnt.n}
    _ = !buildah rm {WK_CTN_NAME}

!mkdir -p {DNF_CACHE}

##### dnf5 distro-sync #####
print('\n', f'{SEP} Run dnf distro-sync ... {SEP}')
_ = !buildah unshare buildah from --name {WK_CTN_NAME} scratch
wk_mnt = !buildah unshare buildah mount {WK_CTN_NAME}
print(wk_mnt.s, '\n')

dnf_cmd_distro_sync = LF_DNF_CMD_DISTRO_SYNC(wk_mnt.s, dnf_repos)
print(dnf_cmd_distro_sync)
!{dnf_cmd_distro_sync}

!buildah unshare rm -rf {wk_mnt.n}
_ = !buildah rm {WK_CTN_NAME}
#####

buildah_script_sh = \
f'''#!/bin/sh
#set -x;
#id;

ctn=$(buildah from --name {WK_CTN_NAME} scratch)
wk_mnt=$(buildah mount {WK_CTN_NAME})

{DNF_CMD} install -y \\
    --use-host-config \\
    --installroot ${{wk_mnt}} \\
    --releasever {RELEASE_VER} \\
    --setopt install_weak_deps=false \\
    --nodocs \\
    --setopt cachedir='{DNF_CACHE}' \\
    --disablerepo='*' --enablerepo='{" ".join(dnf_repos)}' \\
    {" ".join(inst_pkgs)}{' 2>/dev/null' if not DNF_DOWNLOAD_PROGRESS_OUTPUT else ''};
'''
if NEW_CTN_NAME.endswith('-minimal'):
    buildah_script_sh += \
    f'''
echo '%_install_langs en_US.UTF-8' > /etc/rpm/macros.image-language-conf;
{DNF_CMD} reinstall -y \\
    --use-host-config \\
    --installroot ${{wk_mnt}} \\
    --releasever {RELEASE_VER} \\
    --setopt install_weak_deps=false \\
    --nodocs \\
    --setopt cachedir='{DNF_CACHE}' \\
    --disablerepo='*' --enablerepo='{" ".join(dnf_repos)}' \\
    {" ".join(reinst_pkgs)}{' 2>/dev/null' if not DNF_DOWNLOAD_PROGRESS_OUTPUT else ''};
    '''
buildah_script_sh += \
f'''
{DNF_CMD} clean all --installroot ${{wk_mnt}};

rm -rf ${{wk_mnt}}/var/cache/dnf ${{wk_mnt}}/var/log/dnf* ${{wk_mnt}}/var/lib/dnf;
#rm -rf ${{wk_mnt}}/var/log/yum.*;
/bin/date +%Y%m%d_%H%M > ${{wk_mnt}}/etc/BUILDTIME;
#echo '%_install_langs C.utf8' > ${{wk_mnt}}/etc/rpm/macros.image-language-conf;
echo 'LANG="C.utf8"' >  ${{wk_mnt}}/etc/locale.conf;
#echo 'container' > ${{wk_mnt}}/etc/dnf/vars/infra;
rm -f ${{wk_mnt}}/etc/machine-id;
touch ${{wk_mnt}}/etc/machine-id;
touch ${{wk_mnt}}/etc/resolv.conf;
touch ${{wk_mnt}}/etc/hostname;
touch ${{wk_mnt}}/etc/.pwd.lock;
chmod 600 ${{wk_mnt}}/etc/.pwd.lock;

#rm -rf ${{wk_mnt}}/usr/share/locale/en* ${{wk_mnt}}/boot ${{wk_mnt}}/dev/null ${{wk_mnt}}/var/log/hawkey.log;
rm -rf ${{wk_mnt}}/boot ${{wk_mnt}}/dev/null ${{wk_mnt}}/var/log/hawkey.log;
find ${{wk_mnt}}/usr/share/locale/* -maxdepth 0 -type d -exec rm -r {{}} \\; ;
find ${{wk_mnt}}/etc/pki/rpm-gpg/* -not -regex '.*\\(3[4-9]\\|4[0-1]\\)\\(-.*\\)?' -exec rm -f {{}} \\; ;

echo '0.0 0 0.0' > ${{wk_mnt}}/etc/adjtime;
echo '0' >> ${{wk_mnt}}/etc/adjtime;
echo 'UTC' >> ${{wk_mnt}}/etc/adjtime;
echo '# This file has been generated by the Anaconda Installer.' > ${{wk_mnt}}/etc/sysconfig/sshd-permitrootlogin;
echo '# Allow root to log in using ssh. Remove this file to opt-out.' >> ${{wk_mnt}}/etc/sysconfig/sshd-permitrootlogin;
echo 'PERMITROOTLOGIN="-oPermitRootLogin=yes"' >> ${{wk_mnt}}/etc/sysconfig/sshd-permitrootlogin;
echo 'KEYMAP="us"' > ${{wk_mnt}}/etc/vconsole.conf;
echo 'FONT="eurlatgr"' >> ${{wk_mnt}}/etc/vconsole.conf;
mkdir -p ${{wk_mnt}}/run/lock;
cd ${{wk_mnt}}/etc;
ln -s ../usr/share/zoneinfo/UTC localtime;
du -hs ${{wk_mnt}};

buildah unmount {WK_CTN_NAME};
buildah config --cmd sh {WK_CTN_NAME};
buildah commit {WK_CTN_NAME} localhost/{NEW_CTN_NAME};
'''

# https://github.com/containers/buildah/blob/main/docs/buildah-unshare.1.md
# https://github.com/containers/buildah/blob/main/docs/tutorials/01-intro.md
print('\n', f'{SEP} Run buildah_script.sh ... {SEP}')
%store buildah_script_sh >buildah_script.sh
#sys.exit(0)
!buildah unshare sh buildah_script.sh
!buildah rm {WK_CTN_NAME}

print('\n', f'{SEP} Container details {SEP}')
!podman image tree localhost/{NEW_CTN_NAME}
!podman run --rm -ti localhost/{NEW_CTN_NAME} sh -c 'cat /etc/redhat-release'


 ========== Run dnf distro-sync ... ==========
/home/tomoyan/.local/share/containers/storage/overlay/9cbcd61395dd1dbe89e0647dd92dfbec7c005490a018e9cce579fa681ca6c303/merged 

dnf distro-sync \
    --use-host-config \
    --releasever 41 \
    --installroot '/home/tomoyan/.local/share/containers/storage/overlay/9cbcd61395dd1dbe89e0647dd92dfbec7c005490a018e9cce579fa681ca6c303/merged/' \
    --setopt install_weak_deps=false \
    --nodocs \
    --setopt cachedir='dnfcache/41' \
    --disablerepo='*' --enablerepo='updates fedora' 2>/dev/null

Nothing to do.

 ========== Run buildah_script.sh ... ==========
Writing 'buildah_script_sh' (str) to file 'buildah_script.sh'.
Package                        Arch   Version                 Reposito      Size
Installing:
 coreutils-single              x86_64 9.5-11.fc41             updates    1.3 MiB
 glibc-minimal-langpack        x86_64 2.40-21.fc41            updates    0.0   B
Installing dependencies:
 audit-libs                    x86_64 4.0.3-1.

## コンテナサイズ確認

In [2]:
import json

imgs_json = !buildah images --json
imgs = json.loads(imgs_json.n) if imgs_json.n != 'null' else []

if NEW_CTN_NAME.endswith('-micro'):
    for ctn_name in [f'fedora{releasever}-micro' for releasever in range(41, 38-1, -1)]:
        if len(imgs) != 0 and \
           len([img['names'] for img in imgs if img['names'] is not None and ctn_name in img['names'][0]]) != 0:
            !podman run --rm -ti localhost/{ctn_name} sh -c 'cat /etc/redhat-release'
            !podman image tree localhost/{ctn_name}
if NEW_CTN_NAME.endswith('-minimal'):
    for ctn_name in [f'fedora{releasever}-minimal' for releasever in range(41, 38-1, -1)]:
        if len(imgs) != 0 and \
           len([img['names'] for img in imgs if img['names'] is not None and ctn_name in img['names'][0]]) != 0:
            !podman run --rm -ti localhost/{ctn_name} sh -c 'cat /etc/redhat-release'
            !podman image tree localhost/{ctn_name}

Fedora release 41 (Forty One)
Image ID: ddf7fa5f8dc7
Tags:     [localhost/fedora41-micro:latest]
Size:     20.12MB
Image Layers
└── ID: c8218d60cf91 Size: 20.12MB Top Layer of: [localhost/fedora41-micro:latest]

Fedora release 40 (Forty)
Image ID: db8e19aa0e4d
Tags:     [localhost/fedora40-micro:latest]
Size:     19.67MB
Image Layers
└── ID: 5d49da5b381f Size: 19.67MB Top Layer of: [localhost/fedora40-micro:latest]

Fedora release 39 (Thirty Nine)
Image ID: 2e391863a966
Tags:     [localhost/fedora39-micro:latest]
Size:     18.76MB
Image Layers
└── ID: e7b4df3a7e67 Size: 18.76MB Top Layer of: [localhost/fedora39-micro:latest]

Fedora release 38 (Thirty Eight)
Image ID: ee7670e98272
Tags:     [localhost/fedora38-micro:latest]
Size:     22.08MB
Image Layers
└── ID: 9f852d8c4fb7 Size: 22.08MB Top Layer of: [localhost/fedora38-micro:latest]

